In [1]:
# Tensorflow / Keras

from tensorflow import keras # for building Neural Networks
import tensorflow as tf
print('Tensorflow/Keras: %s' % keras.__version__) # print version
from keras.models import Sequential # for creating a linear stack of layers for our Neural Network
from keras import Input # for instantiating a keras tensor
from keras.layers import Bidirectional, GRU, RepeatVector, Dense, TimeDistributed ,LSTM# for creating layers inside the Neural Network
# Data manipulation
import pandas as pd # for data manipulation
print('pandas: %s' % pd.__version__) # print version
import numpy as np # for data manipulation
print('numpy: %s' % np.__version__) # print version

# Sklearn
import sklearn
print('sklearn: %s' % sklearn.__version__) # print version
from sklearn.preprocessing import MinMaxScaler # for feature scaling

# Visualization
import plotly 
import plotly.express as px
import plotly.graph_objects as go
print('plotly: %s' % plotly.__version__) # print version

Tensorflow/Keras: 2.8.0
pandas: 1.3.2
numpy: 1.20.3
sklearn: 1.2.2
plotly: 5.7.0


In [2]:
csv_path = r'C:\Users\Nassoh\Desktop\DataSienceMyProject\BTC Price\Data\BTCUSD_day.csv'

In [3]:
# Read in the BTC data csv - keep only the columns we need
df=pd.read_csv(csv_path, encoding='utf-8')



In [4]:
# Convert dates to Year-Month-Day-Hour-Minute
df['Year-Month-Day-Hour-Minute']= (pd.to_datetime(df['date'], yearfirst=True)).dt.strftime('%Y/%m/%d')

# Show a snaphsot of data
df

unix             date   symbol      open      high       low  \
0     1682380800   4/25/2023 0:00  BTC/USD  27515.00  27525.00  27509.00   
1     1682294400   4/24/2023 0:00  BTC/USD  27594.00  27998.00  26981.00   
2     1682208000   4/23/2023 0:00  BTC/USD  27820.00  27820.00  27347.00   
3     1682121600   4/22/2023 0:00  BTC/USD  27253.00  27883.00  27137.00   
4     1682035200   4/21/2023 0:00  BTC/USD  28240.00  28362.00  27140.00   
...          ...              ...      ...       ...       ...       ...   
3066  1417478400   12/2/2014 0:00  BTC/USD    378.39    382.86    375.23   
3067  1417392000   12/1/2014 0:00  BTC/USD    376.40    382.31    373.03   
3068  1417305600  11/30/2014 0:00  BTC/USD    376.57    381.99    373.32   
3069  1417219200  11/29/2014 0:00  BTC/USD    376.42    386.60    372.25   
3070  1417132800  11/28/2014 0:00  BTC/USD    363.59    381.34    360.57   

         close    Volume BTC    Volume USD Year-Month-Day-Hour-Minute  
0     27521.00  1.026468e+00  2.824943e+04                 2023/04/25  
1     27512.00  2.236655e+03  6.153485e+07                 2023/04/24  
2     27596.00  7.980455e+02  2.202286e+07                 2023/04/23  
3     27817.00  1.010447e+03  2.810761e+07                 2023/04/22  
4     27254.00  2.455900e+03  6.693309e+07                 2023/04/21  
...        ...           ...           ...                        ...  
3066    379.25  2.593576e+06  6.832530e+03                 2014/12/02  
3067    378.39  2.520662e+06  6.660560e+03                 2014/12/01  
3068    373.34  1.145567e+06  3.046330e+03                 2014/11/30  
3069    376.72  2.746157e+06  7.245190e+03                 2014/11/29  
3070    376.28  3.220878e+06  8.617150e+03                 2014/11/28  

[3071 rows x 10 columns]

In [5]:
# Derive median daily temperature (mid point between Daily Max and Daily Min)
df['Med']=df[['low', 'high']].median(axis=1)
df


unix             date   symbol      open      high       low  \
0     1682380800   4/25/2023 0:00  BTC/USD  27515.00  27525.00  27509.00   
1     1682294400   4/24/2023 0:00  BTC/USD  27594.00  27998.00  26981.00   
2     1682208000   4/23/2023 0:00  BTC/USD  27820.00  27820.00  27347.00   
3     1682121600   4/22/2023 0:00  BTC/USD  27253.00  27883.00  27137.00   
4     1682035200   4/21/2023 0:00  BTC/USD  28240.00  28362.00  27140.00   
...          ...              ...      ...       ...       ...       ...   
3066  1417478400   12/2/2014 0:00  BTC/USD    378.39    382.86    375.23   
3067  1417392000   12/1/2014 0:00  BTC/USD    376.40    382.31    373.03   
3068  1417305600  11/30/2014 0:00  BTC/USD    376.57    381.99    373.32   
3069  1417219200  11/29/2014 0:00  BTC/USD    376.42    386.60    372.25   
3070  1417132800  11/28/2014 0:00  BTC/USD    363.59    381.34    360.57   

         close    Volume BTC    Volume USD Year-Month-Day-Hour-Minute  \
0     27521.00  1.026468e+00  2.824943e+04                 2023/04/25   
1     27512.00  2.236655e+03  6.153485e+07                 2023/04/24   
2     27596.00  7.980455e+02  2.202286e+07                 2023/04/23   
3     27817.00  1.010447e+03  2.810761e+07                 2023/04/22   
4     27254.00  2.455900e+03  6.693309e+07                 2023/04/21   
...        ...           ...           ...                        ...   
3066    379.25  2.593576e+06  6.832530e+03                 2014/12/02   
3067    378.39  2.520662e+06  6.660560e+03                 2014/12/01   
3068    373.34  1.145567e+06  3.046330e+03                 2014/11/30   
3069    376.72  2.746157e+06  7.245190e+03                 2014/11/29   
3070    376.28  3.220878e+06  8.617150e+03                 2014/11/28   

            Med  
0     27517.000  
1     27489.500  
2     27583.500  
3     27510.000  
4     27751.000  
...         ...  
3066    379.045  
3067    377.670  
3068    377.655  
3069    379.425  
3070    370.955  

[3071 rows x 11 columns]

In [6]:
# Create a copy of an original dataframe
DF=df[['symbol','Year-Month-Day-Hour-Minute','Med']].copy()
# Display the new dataframe
DF



BTC=DF.pivot(index=['symbol'], columns='Year-Month-Day-Hour-Minute')['Med']
BTC


Year-Month-Day-Hour-Minute  2014/11/28  2014/11/29  2014/11/30  2014/12/01  \
symbol                                                                       
BTC/USD                        370.955     379.425     377.655      377.67   

Year-Month-Day-Hour-Minute  2014/12/02  2014/12/03  2014/12/04  2014/12/05  \
symbol                                                                       
BTC/USD                        379.045     378.615       369.5      370.94   

Year-Month-Day-Hour-Minute  2014/12/06  2014/12/07  ...  2023/04/16  \
symbol                                              ...               
BTC/USD                         374.15      375.33  ...     30362.0   

Year-Month-Day-Hour-Minute  2023/04/17  2023/04/18  2023/04/19  2023/04/20  \
symbol                                                                       
BTC/USD                        29792.0     29802.5     29513.0     28551.5   

Year-Month-Day-Hour-Minute  2023/04/21  2023/04/22  2023/04/23  2023/04/24  \
symbol                                                                       
BTC/USD                        27751.0     27510.0     27583.5     27489.5   

Year-Month-Day-Hour-Minute  2023/04/25  
symbol                                  
BTC/USD                        27517.0  

[1 rows x 3071 columns]

In [7]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=BTC.loc['BTC/USD', :].index, 
                         y=BTC.loc['BTC/USD', :].values,
                         mode='lines',
                         name='BTC',
                         opacity=0.8,
                         line=dict(width=1)
                         ))

# Change chart background color
fig.update_layout(dict(plot_bgcolor = 'white'), showlegend=True)

# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Year-Month-Day-Hour'
                )

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Price'
                )

# Set figure title
fig.update_layout(title=dict(text="CRYRMH_DATA", font=dict(color='black')))

fig.show()

In [8]:
def shaping(datain, timestep):
    
    # Loop through each location
    for CRYPTO in datain.index:
        datatmp = datain[datain.index==CRYPTO].copy()
    
        # Convert input dataframe to array and flatten
        arr=datatmp.to_numpy().flatten() 
        
        cnt=0
        for mth in range(0, len(datatmp.columns)-(2*timestep)+1): # Define range 
            cnt=cnt+1 # Gives us the number of samples. Later used to reshape the data
            X_start=mth # Start month for inputs of each sample
            X_end=mth+timestep # End month for inputs of each sample
            Y_start=mth+timestep # Start month for targets of each sample. Note, start is inclusive and end is exclusive, that's why X_end and Y_start is the same number
            Y_end=mth+2*timestep # End month for targets of each sample.  

            # Assemble input and target arrays containing all samples
            if mth==0:
                X_comb=arr[X_start:X_end]
                Y_comb=arr[Y_start:Y_end]
            else: 
                X_comb=np.append(X_comb, arr[X_start:X_end])
                Y_comb=np.append(Y_comb, arr[Y_start:Y_end])

        # Reshape input and target arrays 
        X_loc=np.reshape(X_comb, (cnt, timestep, 1))
        Y_loc=np.reshape(Y_comb, (cnt, timestep, 1))
        
        # Append an array for each location to the master array
        if CRYPTO==datain.index[0]:
            X_out=X_loc
            Y_out=Y_loc
        else:
            X_out=np.concatenate((X_out, X_loc), axis=0)
            Y_out=np.concatenate((Y_out, Y_loc), axis=0)
            
    return X_out, Y_out

In [9]:
##### Step 1 - Specify parameters

timestep=18
scaler = MinMaxScaler(feature_range=(-1, 1))


In [10]:
##### Step 2 - Prepare data

# Split data into train and test dataframes

train=BTC.iloc[:, 0:-12*timestep].copy()
test=BTC.iloc[:, -12*timestep:].copy()


print(train.shape)
print(test.shape)


(1, 2855)
(1, 216)


In [13]:
test

Year-Month-Day-Hour-Minute  2022/09/22  2022/09/23  2022/09/24  2022/09/25  \
symbol                                                                       
BTC/USD                        18954.5     19012.0     19063.0     18909.0   

Year-Month-Day-Hour-Minute  2022/09/26  2022/09/27  2022/09/28  2022/09/29  \
symbol                                                                       
BTC/USD                        19001.5     19601.5     19115.5     19241.0   

Year-Month-Day-Hour-Minute  2022/09/30  2022/10/01  ...  2023/04/16  \
symbol                                              ...               
BTC/USD                        19661.5     19329.0  ...     30362.0   

Year-Month-Day-Hour-Minute  2023/04/17  2023/04/18  2023/04/19  2023/04/20  \
symbol                                                                       
BTC/USD                        29792.0     29802.5     29513.0     28551.5   

Year-Month-Day-Hour-Minute  2023/04/21  2023/04/22  2023/04/23  2023/04/24  \
symbol                                                                       
BTC/USD                        27751.0     27510.0     27583.5     27489.5   

Year-Month-Day-Hour-Minute  2023/04/25  
symbol                                  
BTC/USD                        27517.0  

[1 rows x 216 columns]

In [14]:
# Use fit to train the scaler on the training data only, actual scaling will be done inside reshaping function
scaler.fit(train.to_numpy().reshape(-1, 1))

MinMaxScaler(feature_range=(-1, 1))

In [15]:
# Use previously defined shaping function to reshape the data for GRU
X_train, Y_train = shaping(train,timestep=timestep)
X_test, Y_test = shaping(test,timestep=timestep)


In [16]:
for i in range(1) : 
    print("........................",i+1,"....................")
    print("....................X-Train....................")
    #print(X_train[i])
    print(X_train.shape)
    print("....................Y-Train....................")
    print(Y_train.shape)
    print("....................X_Test....................")
    print(X_test.shape)
    print("....................Y_Test....................")
    print(Y_test.shape)
    #

........................ 1 ....................
....................X-Train....................
(2820, 18, 1)
....................Y-Train....................
(2820, 18, 1)
....................X_Test....................
(181, 18, 1)
....................Y_Test....................
(181, 18, 1)


In [15]:
import plotly.express as px

fig = px.scatter(x=X_train[1].flatten(),y=Y_train[1].flatten())
# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='X'
                )

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Y'
                )
fig.show()

In [17]:
fig = go.Figure()

for i in range(5):
    fig.add_trace(go.Scatter(x=BTC.loc['BTC/USD', :].index, 
                         y=scaler.inverse_transform(X_train[i].reshape(-1,1)).flatten(),
                         mode='lines',
                         name='BTC',
                         opacity=0.8,
                         line=dict(width=1)
                         ))

# Change chart background color
fig.update_layout(dict(plot_bgcolor = 'white'), showlegend=True)

# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Year-Month-Day-Hour'
                )

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Price'
                )

# Set figure title
fig.update_layout(title=dict(text="X_train", font=dict(color='black')))

fig.show()

In [18]:
fig = go.Figure()
for i in range(5):
    fig.add_trace(go.Scatter(x=BTC.loc['BTC/USD', :].index, 
                         y=scaler.inverse_transform(Y_train[i].reshape(-1,1)).flatten(),
                         mode='lines',
                         name='BTC',
                         opacity=0.8,
                         line=dict(width=1)
                         ))

# Change chart background color
fig.update_layout(dict(plot_bgcolor = 'white'), showlegend=True)

# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Year-Month-Day-Hour'
                )

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Price'
                )

# Set figure title
fig.update_layout(title=dict(text="Y_train", font=dict(color='black')))

fig.show()

In [19]:
fig = go.Figure()


fig.add_trace(go.Scatter(x=BTC.loc['BTC/USD', :].index, 
                         y=scaler.inverse_transform(X_train.reshape(-1,1)).flatten(),
                         mode='lines',
                         name='BTC',
                         opacity=0.8,
                         line=dict(width=1)
                         ))

# Change chart background color
fig.update_layout(dict(plot_bgcolor = 'white'), showlegend=True)

# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Year-Month-Day-Hour'
                )

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Price'
                )

# Set figure title
fig.update_layout(title=dict(text="X_train", font=dict(color='black')))

fig.show()

In [20]:
fig = go.Figure()


fig.add_trace(go.Scatter(x=BTC.loc['BTC/USD', :].index, 
                         y=scaler.inverse_transform(Y_train.reshape(-1,1)).flatten(),
                         mode='lines',
                         name='BTC',
                         opacity=0.8,
                         line=dict(width=1)
                         ))

# Change chart background color
fig.update_layout(dict(plot_bgcolor = 'white'), showlegend=True)

# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Year-Month-Day-Hour'
                )

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Price'
                )

# Set figure title
fig.update_layout(title=dict(text="Y_train", font=dict(color='black')))

fig.show()

In [21]:
fig = go.Figure()

for i in range(11):
    fig.add_trace(go.Scatter(x=BTC.loc['BTC/USD', :].index, 
                         y=scaler.inverse_transform(X_test[(i)*18].reshape(-1,1)).flatten(),
                         mode='lines',
                         name='BTC',
                         opacity=0.8,
                         line=dict(width=1)
                         ))

# Change chart background color
fig.update_layout(dict(plot_bgcolor = 'white'), showlegend=True)

# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Year-Month-Day-Hour'
                )

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Price'
                )

# Set figure title
fig.update_layout(title=dict(text="X_test", font=dict(color='black')))

fig.show()

In [22]:
fig = go.Figure()

for i in range(11):
    fig.add_trace(go.Scatter(x=BTC.loc['BTC/USD', :].index, 
                         y=scaler.inverse_transform(Y_test[i*18].reshape(-1,1)).flatten(),
                         mode='lines',
                         name='BTC',
                         opacity=0.8,
                         line=dict(width=1)
                         ))

# Change chart background color
fig.update_layout(dict(plot_bgcolor = 'white'), showlegend=True)

# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Year-Month-Day-Hour'
                )

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Price'
                )

# Set figure title
fig.update_layout(title=dict(text="Y_test", font=dict(color='black')))

fig.show()

In [23]:
from keras.callbacks import ModelCheckpoint

filepath = 'CC18A.hdf5'
checkpoint = ModelCheckpoint(filepath=filepath,monitor='loss',verbose=1,save_best_only=True,mode='min')
callbacks = [checkpoint]

In [24]:
##### Step 3 - Specify the structure of a Neural Network
model = Sequential(name="GRU") # Model
model.add(Input(shape=(X_train.shape[1],X_train.shape[2]), name='Input-Layer')) # Input Layer - need to speicfy the shape of inputs
model.add(Bidirectional(GRU(units=32, activation='tanh', recurrent_activation='sigmoid', stateful=False), name='Hidden-GRU-Encoder-Layer')) # Encoder Layer
model.add(RepeatVector(X_train.shape[1], name='Repeat-Vector-Layer')) # Repeat Vector
model.add(Bidirectional(GRU(units=32, activation='tanh', recurrent_activation='sigmoid', stateful=False, return_sequences=True), name='Hidden-GRU-Decoder-Layer')) # Decoder Layer
model.add(TimeDistributed(Dense(units=1, activation='linear'), name='Output-Layer')) # Output Layer, Linear(x) = x


In [25]:
model.compile(optimizer='adam', # default='rmsprop', an algorithm to be used in backpropagation
              loss='mean_squared_error', # Loss function to be optimized. A string (name of loss function), or a tf.keras.losses.Loss instance.
              metrics=['MeanAbsoluteError'], # List of metrics to be evaluated by the model during training and testing. Each of this can be a string (name of a built-in function), function or a tf.keras.metrics.Metric instance. 
              loss_weights=None, # default=None, Optional list or dictionary specifying scalar coefficients (Python floats) to weight the loss contributions of different model outputs.
              weighted_metrics=None, # default=None, List of metrics to be evaluated and weighted by sample_weight or class_weight during training and testing.
              run_eagerly=None, # Defaults to False. If True, this Model's logic will not be wrapped in a tf.function. Recommended to leave this as None unless your Model cannot be run inside a tf.function.
              steps_per_execution=None # Defaults to 1. The number of batches to run during each tf.function call. Running multiple batches inside a single tf.function call can greatly improve performance on TPUs or small models with a large Python overhead.
             )

In [26]:
history = model.fit(X_train, # input data
                    Y_train, # target data
                    batch_size=1, # Number of samples per gradient update. If unspecified, batch_size will default to 32.
                    epochs=99, # default=1, Number of epochs to train the model. An epoch is an iteration over the entire x and y data provided
                    verbose=1, # default='auto', ('auto', 0, 1, or 2). Verbosity mode. 0 = silent, 1 = progress bar, 2 = one line per epoch. 'auto' defaults to 1 for most cases, but 2 when used with ParameterServerStrategy.
                    callbacks=callbacks, # default=None, list of callbacks to apply during training. See tf.keras.callbacks
                    #validation_split=0.2, # default=0.0, Fraction of the training data to be used as validation data. The model will set apart this fraction of the training data, will not train on it, and will evaluate the loss and any model metrics on this data at the end of each epoch. 
                    validation_data=(X_test, Y_test), # default=None, Data on which to evaluate the loss and any model metrics at the end of each epoch. 
                    shuffle=True, # default=True, Boolean (whether to shuffle the training data before each epoch) or str (for 'batch').
                    class_weight=None, # default=None, Optional dictionary mapping class indices (integers) to a weight (float) value, used for weighting the loss function (during training only). This can be useful to tell the model to "pay more attention" to samples from an under-represented class.
                    sample_weight=None, # default=None, Optional Numpy array of weights for the training samples, used for weighting the loss function (during training only).
                    initial_epoch=0, # Integer, default=0, Epoch at which to start training (useful for resuming a previous training run).
                    steps_per_epoch=None, # Integer or None, default=None, Total number of steps (batches of samples) before declaring one epoch finished and starting the next epoch. When training with input tensors such as TensorFlow data tensors, the default None is equal to the number of samples in your dataset divided by the batch size, or 1 if that cannot be determined. 
                    validation_steps=None, # Only relevant if validation_data is provided and is a tf.data dataset. Total number of steps (batches of samples) to draw before stopping when performing validation at the end of every epoch.
                    validation_batch_size=None, # Integer or None, default=None, Number of samples per validation batch. If unspecified, will default to batch_size.
                    validation_freq=1, # default=1, Only relevant if validation data is provided. If an integer, specifies how many training epochs to run before a new validation run is performed, e.g. validation_freq=2 runs validation every 2 epochs.
                    max_queue_size=10, # default=10, Used for generator or keras.utils.Sequence input only. Maximum size for the generator queue. If unspecified, max_queue_size will default to 10.
                    workers=1, # default=1, Used for generator or keras.utils.Sequence input only. Maximum number of processes to spin up when using process-based threading. If unspecified, workers will default to 1.
                    use_multiprocessing=True, # default=False, Used for generator or keras.utils.Sequence input only. If True, use process-based threading. If unspecified, use_multiprocessing will default to False. 
                   )

Epoch 1/99
2813/2820 [============================>.] - ETA: 0s - loss: 441240384.0000 - mean_absolute_error: 12972.3721
Epoch 1: loss improved from inf to 441045760.00000, saving model to CC18A.hdf5
2820/2820 [==============================] - 26s 8ms/step - loss: 441045760.0000 - mean_absolute_error: 12967.2715 - val_loss: 465184992.0000 - val_mean_absolute_error: 21161.8496
Epoch 2/99
2816/2820 [============================>.] - ETA: 0s - loss: 438676608.0000 - mean_absolute_error: 12865.0156
Epoch 2: loss improved from 441045760.00000 to 438105280.00000, saving model to CC18A.hdf5
2820/2820 [==============================] - 20s 7ms/step - loss: 438105280.0000 - mean_absolute_error: 12853.6299 - val_loss: 460426688.0000 - val_mean_absolute_error: 21049.1152
Epoch 3/99
2820/2820 [==============================] - ETA: 0s - loss: 435234208.0000 - mean_absolute_error: 12751.2070
Epoch 3: loss improved from 438105280.00000 to 435234208.00000, saving model to CC18A.hdf5
2820/2820 [=====

KeyboardInterrupt: 

In [27]:
pred_test = model.predict(X_test)
pred = model.predict(X_train)

In [28]:
##### Step 7 - Print Performance Summary
print("")
print('-------------------- Model Summary --------------------')
model.summary() # print model summary
print("")


-------------------- Model Summary --------------------
Model: "GRU"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 Hidden-GRU-Encoder-Layer (B  (None, 64)               6720      
 idirectional)                                                   
                                                                 
 Repeat-Vector-Layer (Repeat  (None, 18, 64)           0         
 Vector)                                                         
                                                                 
 Hidden-GRU-Decoder-Layer (B  (None, 18, 64)           18816     
 idirectional)                                                   
                                                                 
 Output-Layer (TimeDistribut  (None, 18, 1)            65        
 ed)                                                             
                                                                 
Total 

In [29]:
print('-------------------- Weights and Biases --------------------')
print("Too many parameters to print but you can use the code provided if needed")
print("")
i=0
for layer in model.layers:
    i=i+1
    print(i)
    print(layer.name)
    
        
print("")

-------------------- Weights and Biases --------------------
Too many parameters to print but you can use the code provided if needed

1
Hidden-GRU-Encoder-Layer
2
Repeat-Vector-Layer
3
Hidden-GRU-Decoder-Layer
4
Output-Layer



In [30]:
# Plot average monthly temperatures (actual and predicted) for test (out of time) data
fig = go.Figure()

# Trace for predicted temperatures
for i in range(0,11):
    fig.add_trace(go.Scatter(x=np.array([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48]),
                             # Need to inverse transform the predictions before plotting
                             y=scaler.inverse_transform(Y_train[18*i].reshape(-1,1)).flatten(), 
                             mode='lines', 
                             name=' Prediction',
                             opacity=1,
                             line=dict(width=2, dash='dot')
                            ))
# # Trace for predicted temperatures
# for i in range(0,pred_test.shape[0]):
#     fig.add_trace(go.Scatter(x=np.array([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48]),
#                              # Need to inverse transform the predictions before plotting
#                              y=scaler.inverse_transform(pred_test[144].reshape(-1,1)).flatten(), 
#                              mode='lines', 
#                              name=' Prediction',
#                              opacity=1,
#                              line=dict(width=2, dash='dot')
#                             ))
    


# Change chart background color
fig.update_layout(dict(plot_bgcolor = 'white'))

# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Year-Month-Day-hour'
                )

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='PRICE'
                )

# Set figure title
fig.update_layout(title=dict(text="y_train", font=dict(color='black')))
fig.show()


In [31]:
# Plot average monthly temperatures (actual and predicted) for test (out of time) data
fig = go.Figure()

# Trace for predicted temperatures
for i in range(0,11):
    fig.add_trace(go.Scatter(x=np.array([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48]),
                             # Need to inverse transform the predictions before plotting
                             y=scaler.inverse_transform(pred[18*i].reshape(-1,1)).flatten(), 
                             mode='lines', 
                             name=' Prediction',
                             opacity=1,
                             line=dict(width=2, dash='dot')
                            ))
# # Trace for predicted temperatures
# for i in range(0,pred_test.shape[0]):
#     fig.add_trace(go.Scatter(x=np.array([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48]),
#                              # Need to inverse transform the predictions before plotting
#                              y=scaler.inverse_transform(pred_test[144].reshape(-1,1)).flatten(), 
#                              mode='lines', 
#                              name=' Prediction',
#                              opacity=1,
#                              line=dict(width=2, dash='dot')
#                             ))
    


# Change chart background color
fig.update_layout(dict(plot_bgcolor = 'white'))

# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Year-Month-Day-hour'
                )

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='PRICE'
                )

# Set figure title
fig.update_layout(title=dict(text="pred on y_train", font=dict(color='black')))
fig.show()


In [32]:
# Plot average monthly temperatures (actual and predicted) for test (out of time) data
fig = go.Figure()

# Trace for predicted temperatures
for i in range(0,3):
    fig.add_trace(go.Scatter(x=np.array([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48]),
                             # Need to inverse transform the predictions before plotting
                             y=scaler.inverse_transform(Y_test[i*18].reshape(-1,1)).flatten(), 
                             mode='lines', 
                             name=' Prediction',
                             opacity=1,
                             line=dict(width=2, dash='dot')
                            ))
# # Trace for predicted temperatures
# for i in range(0,pred_test.shape[0]):
#     fig.add_trace(go.Scatter(x=np.array([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48]),
#                              # Need to inverse transform the predictions before plotting
#                              y=scaler.inverse_transform(pred_test[144].reshape(-1,1)).flatten(), 
#                              mode='lines', 
#                              name=' Prediction',
#                              opacity=1,
#                              line=dict(width=2, dash='dot')
#                             ))
# Trace for predicted temperatures
for i in range(0,3):
    fig.add_trace(go.Scatter(x=np.array([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48]),
                             # Need to inverse transform the predictions before plotting
                             y=scaler.inverse_transform(pred_test[i*18].reshape(-1,1)).flatten(), 
                             mode='lines', 
                             name=' Y_test',
                             opacity=1,
                             line=dict(width=2, dash='dot')
                            ))
    


# Change chart background color
fig.update_layout(dict(plot_bgcolor = 'white'))

# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Year-Month-Day-hour'
                )

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='PRICE'
                )

# Set figure title
fig.update_layout(title=dict(text="Prediction", font=dict(color='black')))
fig.show()


In [33]:
from keras import models

model_v = models.load_model(filepath)

pred_test = model_v.predict(X_test)
pred = model_v.predict(X_train)

In [34]:
# Plot average monthly temperatures (actual and predicted) for test (out of time) data
fig = go.Figure()

# Trace for predicted temperatures
for i in range(0,3):
    fig.add_trace(go.Scatter(x=np.array([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48]),
                             # Need to inverse transform the predictions before plotting
                             y=scaler.inverse_transform(Y_test[i*18].reshape(-1,1)).flatten(), 
                             mode='lines', 
                             name=' Y_test',
                             opacity=1,
                             line=dict(width=1)
                            ))
# # Trace for predicted temperatures
# for i in range(0,pred_test.shape[0]):
#     fig.add_trace(go.Scatter(x=np.array([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48]),
#                              # Need to inverse transform the predictions before plotting
#                              y=scaler.inverse_transform(pred_test[144].reshape(-1,1)).flatten(), 
#                              mode='lines', 
#                              name=' Prediction',
#                              opacity=1,
#                              line=dict(width=2, dash='dot')
#                             ))
# Trace for predicted temperatures
for i in range(0,3):
    fig.add_trace(go.Scatter(x=np.array([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48]),
                             # Need to inverse transform the predictions before plotting
                             y=scaler.inverse_transform(pred_test[i*18].reshape(-1,1)).flatten(), 
                             mode='lines', 
                             name=' pred_test',
                             opacity=1,
                             line=dict(width=2, dash='dot')
                            ))
    


# Change chart background color
fig.update_layout(dict(plot_bgcolor = 'white'))

# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='Year-Month-Day-hour'
                )

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black',
                 title='PRICE'
                )

# Set figure title
fig.update_layout(title=dict(text="Prediction", font=dict(color='black')))
fig.show()
